In [10]:
import json
import os
import hashlib
from tqdm import tqdm
import shutil
import cv2
import numpy as np

## Restore duplicates variable from duplicates.json

In [6]:
def restore_duplicates_from_json():
        """
        Restores the list of duplicates from the json file
        """
        print("Restoring duplicates from json file...") 
        all_duplicates = None
        duplicates_file_path = os.path.join('C:/Users/nello/Desktop/TESI_CODICE/EDA/method_1/duplicates/all_duplicates.json')
        with open(duplicates_file_path, 'r') as file:
            all_duplicates = json.load(file)
        print("Done")
        return all_duplicates

In [3]:
all_duplicates = restore_duplicates_from_json()
print(all_duplicates[:10])

Restoring duplicates from json file...
Done
['cb2m58f', '8wppd2', '2lf5ko', 'cawnmss', '6h47ct', 'd3mhh6a', '13ltj1', 'cjbnia', 'chc3rfz', 'cbp2yz4']


## Copy the duplicates images inside all_duplicates into a destination folder called all_duplicate_images

In [5]:
def copy_images(image_names, source_folder, destination_folder):
    for image_name in image_names:
        source_path = os.path.join(source_folder, f"{image_name}.jpg")
        destination_path = os.path.join(destination_folder, f"{image_name}.jpg")

        try:
            shutil.copyfile(source_path, destination_path)
            print(f"Successfully copied {image_name}.jpg")
        except FileNotFoundError:
            print(f"Error: {image_name}.jpg not found in {source_folder}")

In [8]:
source_folder = "C:/Users/nello/Desktop/TESI_CODICE/dataset/public_image_set"
destination_folder = "C:/Users/nello/Desktop/TESI_CODICE/EDA/method_1/all_duplicates_images"

os.makedirs(destination_folder, exist_ok=True)
copy_images(all_duplicates, source_folder, destination_folder)

Successfully copied cb2m58f.jpg
Successfully copied 8wppd2.jpg
Successfully copied 2lf5ko.jpg
Successfully copied cawnmss.jpg
Successfully copied 6h47ct.jpg
Successfully copied d3mhh6a.jpg
Successfully copied 13ltj1.jpg
Successfully copied cjbnia.jpg
Successfully copied chc3rfz.jpg
Successfully copied cbp2yz4.jpg
Successfully copied d6px9g.jpg
Successfully copied chuxits.jpg
Successfully copied 199h1k.jpg
Successfully copied csb6xx.jpg
Successfully copied cj6w5h.jpg
Successfully copied e5fi6f9.jpg
Successfully copied aze0h1.jpg
Successfully copied zwoue.jpg
Successfully copied 15q4c9.jpg
Successfully copied e1gn3ci.jpg
Successfully copied cov4mbc.jpg
Successfully copied 1lklu5.jpg
Successfully copied cczrjnv.jpg
Successfully copied cm1s01o.jpg
Successfully copied 4dq8wq.jpg
Successfully copied 2lqial.jpg
Successfully copied dewujyh.jpg
Successfully copied cz547kb.jpg
Successfully copied f3swcw3.jpg
Successfully copied celsp56.jpg
Successfully copied cjl7kbt.jpg
Successfully copied diox

## Detect images containing 'humans' inside the all_duplicates_images folder

In [30]:
net = cv2.dnn.readNet('yolov3.weights', 'yolov3.cfg')
classes = []
with open('coco.names', 'r') as f:
    classes = [line.strip() for line in f.readlines()]
output_layers = net.getUnconnectedOutLayersNames()

def detect_human_yolo(image_path, confidence_threshold=0.7):
    try:
        image = cv2.imread(image_path)
        blob = cv2.dnn.blobFromImage(image, 1/255.0, (416, 416), swapRB=True, crop=False)
        net.setInput(blob)
        #forward pass
        detections = net.forward(output_layers)

        for detection in detections:
            scores = detection[:, 5:]
            class_ids = np.argmax(scores, axis=1)
            confidences = scores[np.arange(len(class_ids)), class_ids]

            #filter detections based on confidence and class_id
            mask = (confidences > confidence_threshold) & (class_ids == 0)  #class 0 corresponds to "person" in coco.names
            if np.any(mask):
                return True
        # case no human detected
        return False
    
    except Exception as e:
        return False


inference single img test

In [ ]:
image_path = 'C:/Users/nello/Desktop/TESI_CODICE/EDA/method_1/all_duplicates_images/1ogg8g.jpg'

if detect_human_yolo(image_path):
    print("Human detected in the image.")
else:
    print("No human detected in the image.")


In [ ]:
def export_to_json(data, json_file_path):
    with open(json_file_path, 'w') as json_file:
        json.dump(data, json_file, indent=4)

In [ ]:
def process_batch(image_files, folder_path, confidence_threshold, batch_index):
    batch_results = [os.path.splitext(image_file)[0] for image_file in image_files if detect_human_yolo(os.path.join(folder_path, image_file), confidence_threshold)]

    # Create the directory if it doesn't exist
    output_directory = 'C:/Users/nello/Desktop/TESI_CODICE/EDA/method_1/duplicates_containing_humans/'
    os.makedirs(output_directory, exist_ok=True)

    # Export the list to a JSON file for this batch
    json_file_path = os.path.join(output_directory, f'duplicates_containing_humans_batch_{batch_index}.json')
    export_to_json(batch_results, json_file_path)
    print(f"Batch {batch_index} - Images containing humans: {batch_results}")
    print(f"Exported to {json_file_path}")

In [ ]:
def collect_images_with_human_presence_batch(folder_path, batch_size=10, confidence_threshold=0.7):
    image_files = [f for f in os.listdir(folder_path)]

    # Process images in batches
    for batch_index, batch in enumerate(tqdm(range(0, len(image_files), batch_size), desc='Batches', unit='batch')):
        batch_files = image_files[batch: batch + batch_size]
        process_batch(batch_files, folder_path, confidence_threshold, batch_index)

In [ ]:
def merge_json_files(merged_json_path, folder_path):
    merged_data = []
    json_files = [f for f in os.listdir(folder_path) if f.endswith('.json')]

    for json_file in json_files:
        json_file_path = os.path.join(folder_path, json_file)

        if os.path.exists(json_file_path):
            with open(json_file_path, 'r') as f:
                data = json.load(f)
                merged_data.extend(data)
        else:
            print(f"File not found: {json_file_path}")

    export_to_json(merged_data, merged_json_path)
    print(f"Merged data exported to {merged_json_path}")

In [31]:
dataset_path = "C:/Users/nello/Desktop/TESI_CODICE/EDA/method_1/all_duplicates_images"
batch_size = 500  
confidence_threshold = 0.7  #confidence to have a human inside the img

#in batches, get list of all images containing humans 
collect_images_with_human_presence_batch(dataset_path, batch_size=batch_size, confidence_threshold=confidence_threshold)

merged_json_path = 'C:/Users/nello/Desktop/TESI_CODICE/EDA/method_1/duplicates_containing_humans/merged_duplicates_containing_humans.json'
merge_json_files(merged_json_path, 'C:/Users/nello/Desktop/TESI_CODICE/EDA/method_1/duplicates_containing_humans/')

Batches:   1%|          | 1/99 [02:33<4:10:17, 153.24s/batch]

0


Batches:   2%|▏         | 2/99 [05:03<4:04:56, 151.51s/batch]

1


Batches:   3%|▎         | 3/99 [07:37<4:03:53, 152.43s/batch]

...

Batches:  99%|█████████▉| 98/99 [4:13:19<02:42, 162.54s/batch]

97


Batches: 100%|██████████| 99/99 [4:14:24<00:00, 154.19s/batch]

98


Merged data exported to C:/Users/nello/Desktop/TESI_CODICE/EDA/method_1/duplicates_containing_humans/merged_duplicates_containing_humans.json


In [4]:
with open('C:/Users/nello/Desktop/TESI_CODICE/EDA/method_1/duplicates_containing_humans/merged_duplicates_containing_humans.json', 'r') as file:
    json = json.load(file)

print(len(json))

14547


## Create a folder duplicates_containing_humans to check the quality of the detection

In [8]:
def restore_duplicates_from_json():
        """
        Restores the list of duplicates from the json file
        """
        print("Restoring duplicates from json file...") 
        duplicates = None
        duplicates_file_path = os.path.join('C:/Users/nello/Desktop/TESI_CODICE/EDA/method_1/duplicates_containing_humans/merged_duplicates_containing_humans.json')
        with open(duplicates_file_path, 'r') as file:
            duplicates = json.load(file)
        print("Done")
        return duplicates

In [11]:
source_folder = "C:/Users/nello/Desktop/TESI_CODICE/EDA/method_1/all_duplicates_images"
destination_folder = "C:/Users/nello/Desktop/TESI_CODICE/EDA/method_1/duplicates_containing_humans_images"

os.makedirs(destination_folder, exist_ok=True)

duplicates_containing_humans = restore_duplicates_from_json()
copy_images(duplicates_containing_humans, source_folder, destination_folder)

Restoring duplicates from json file...
Done
Successfully copied 103crd.jpg
Successfully copied 103neu.jpg
Successfully copied 103ozy.jpg
Successfully copied 106yw5.jpg
Successfully copied 107zkt.jpg
Successfully copied 10c49y.jpg
Successfully copied 10hfrt.jpg
Successfully copied 10ivdc.jpg
Successfully copied 10kltt.jpg
Successfully copied 10piyf.jpg
Successfully copied 10qvbv.jpg
Successfully copied 10re2h.jpg
Successfully copied 10rqk4.jpg
Successfully copied 10ttd2.jpg
Successfully copied 10ujav.jpg
Successfully copied 10unyp.jpg
Successfully copied 10vnl0.jpg
Successfully copied 10x5l9.jpg
Successfully copied 110bop.jpg
Successfully copied 110hkd.jpg
Successfully copied 1139mc.jpg
Successfully copied 115pxg.jpg
Successfully copied 11ef8b.jpg
Successfully copied 11eul6.jpg
Successfully copied 11grh4.jpg
Successfully copied 11icsb.jpg
Successfully copied 11k0bv.jpg
Successfully copied 11nknl.jpg
Successfully copied 11os5t.jpg
Successfully copied 11s1da.jpg
Successfully copied 11sm3d

## Remove all the duplicates containing humans from all_duplicates_images folder

In [16]:
import os
import shutil
import json

all_duplicates_images_path = "C:/Users/nello/Desktop/TESI_CODICE/EDA/method_1/all_duplicates_images"
duplicates_without_humans_images_path = "C:/Users/nello/Desktop/TESI_CODICE/EDA/method_1/duplicates_without_humans_images"
json_file_path = "C:/Users/nello/Desktop/TESI_CODICE/EDA/method_1/duplicates_containing_humans/merged_duplicates_containing_humans.json"
os.makedirs(duplicates_without_humans_images_path, exist_ok=True)

# Read the JSON file
with open(json_file_path) as json_file:
    data = json.load(json_file)

# Ensure "filenames" is a key in the JSON data and is a list
json_filenames = data["filenames"] if "filenames" in data else []

if not isinstance(json_filenames, list):
    raise ValueError("The 'filenames' key in the JSON file should contain a list of filenames.")

# Iterate through files in folder A
for filename in os.listdir(all_duplicates_images_path):
    file_path = os.path.join(all_duplicates_images_path, filename)

    # Check if the filename (without extension) is not in the JSON list
    if filename.split('.')[0] not in json_filenames and os.path.isfile(file_path):
        # Copy the file to folder B
        shutil.copy(file_path, os.path.join(duplicates_without_humans_images_path, filename))


In [17]:
import os
import shutil
import json

def load_excluded_image_names(json_file_path):
    with open(json_file_path, 'r') as json_file:
        return set(json.load(json_file))

def copy_images(folder_a, folder_b, excluded_image_names):
    images_to_copy = [file for file in os.listdir(folder_a) if file.endswith('.jpg') and file[:-4] not in excluded_image_names]

    for image in images_to_copy:
        shutil.copyfile(os.path.join(folder_a, image), os.path.join(folder_b, image))
        print(f"Copying {image} to {folder_b}")

folder_a_path = 'C:/Users/nello/Desktop/TESI_CODICE/EDA/method_1/all_duplicates_images'
folder_b_path = 'C:/Users/nello/Desktop/TESI_CODICE/EDA/method_1/duplicates_without_humans_images'
json_file_path = 'C:/Users/nello/Desktop/TESI_CODICE/EDA/method_1/duplicates_containing_humans/merged_duplicates_containing_humans.json'

excluded_image_names = load_excluded_image_names(json_file_path)
copy_images(folder_a_path, folder_b_path, excluded_image_names)


Copying 100qm6.jpg to C:/Users/nello/Desktop/TESI_CODICE/EDA/method_1/duplicates_without_humans_images
Copying 101j7x.jpg to C:/Users/nello/Desktop/TESI_CODICE/EDA/method_1/duplicates_without_humans_images
Copying 101pol.jpg to C:/Users/nello/Desktop/TESI_CODICE/EDA/method_1/duplicates_without_humans_images
Copying 1028p3.jpg to C:/Users/nello/Desktop/TESI_CODICE/EDA/method_1/duplicates_without_humans_images
Copying 102dal.jpg to C:/Users/nello/Desktop/TESI_CODICE/EDA/method_1/duplicates_without_humans_images
Copying 102udo.jpg to C:/Users/nello/Desktop/TESI_CODICE/EDA/method_1/duplicates_without_humans_images
Copying 1032yi.jpg to C:/Users/nello/Desktop/TESI_CODICE/EDA/method_1/duplicates_without_humans_images
Copying 103577.jpg to C:/Users/nello/Desktop/TESI_CODICE/EDA/method_1/duplicates_without_humans_images
Copying 1036sy.jpg to C:/Users/nello/Desktop/TESI_CODICE/EDA/method_1/duplicates_without_humans_images
Copying 103a9s.jpg to C:/Users/nello/Desktop/TESI_CODICE/EDA/method_1/dup